In [74]:
import pandas as pd


In [75]:
df  = pd.read_parquet('/Users/cultonkoster/Desktop/homework/nwo-case-studies/nlp/df_tweets.parquet')
df2 = pd.read_parquet('/Users/cultonkoster/Desktop/homework/nwo-case-studies/nlp/df_reddit.parquet')


df['created_at']  = pd.to_datetime(df['created_at'])

to_int = lambda timedata: timedata.timestamp()
df['created_utc'] = df.pop('created_at').apply(to_int).astype('int64')


In [76]:
from nltk.tokenize import TweetTokenizer
from nltk.tag import pos_tag
from spacy.lang.en.stop_words import STOP_WORDS
import emoji

STOP_EMOJI = set(emoji.UNICODE_EMOJI.keys())

STOP_WORDS_STOP_EMOJIS = STOP_WORDS.union(STOP_EMOJI)

tweet_tokenizer = TweetTokenizer()


GOOD_TAGS = {
    'NN','NNP','NNPS','NNS'#,'VBD','VB','VBG','VBN','VBP','VBZ'
}


def preprocess_tweets(text: str, group_nouns: bool = True):
    '''
    Pipeline for preprocessing text. The trick to get "elon musk" to appear as one word
    See my notes for future improvements. nltk is by no means the best tokenizer for twitter
    '''
    tokens = tweet_tokenizer.tokenize(text)
    tags = pos_tag(tokens)
    
    text_out: str = ""
    # now we have tags of type Tuple[str,str] and want to keep some of them
    prev_tag: str = ""
    for word,tag in tags:
        
        if tag not in GOOD_TAGS or word[:4] == "http":
            continue
        else:
            # we want to join contiguous proper nouns
            join_nnp = (prev_tag in {"NNP","NNPS"} and prev_tag == tag and group_nouns)
            text_out += "{}{}".format("_" if join_nnp else " ",word)
            prev_tag = tag

    return text_out[1:]


def preprocess_tweets_2(text: str):
    '''
    Another pipeline for preprocessing text. Here the trick is to get all useful words into a sequence/list 
    and then run gensim's phraser on the sentences. This is likely to be more useful as it does not rely on correct
    named entity recognition (or manual grouping). 
    
    Returns a list of words.
    '''
    tokens = tweet_tokenizer.tokenize(text)
    tags = pos_tag(tokens)

    words_out = []
    
    for word,tag in tags:
        
        if tag not in GOOD_TAGS or word[:4] == "http" or len(word) < 3 or word in STOP_WORDS_STOP_EMOJIS:
            continue
        else:
            # we want to join contiguous proper nouns
            words_out.append(word.lower())

    return words_out
    

df["text_preprocessed"] = df["tweet"].apply(preprocess_tweets_2)

# we just wrote a pipeline for tokenizing tweets. We could do a similar one for reddit text,
# but I don't know of any tokenization tools specifically meant for reddit
df2["text_preprocessed"] = df2["body"].apply(preprocess_tweets_2)



In [81]:
#

df

tweet  created_utc  \
0       chill fool lmaoooo no manipulation, just activ...   1605312000   
1       Thanks @DUDEwipes this will help out a lot. Es...   1605830400   
2       Replying to \n@JLPimentelM\n @kendallGBarran1\...   1610328107   
3       IT HAS SPREAD ACROSS THE COUNTRY!\nIf you had ...   1610190443   
4       📣📣Only 2 days left until Ignite Awards 2020 by...   1607904000   
...                                                   ...          ...   
999995  If there was a 24-hour channel that only aired...   1610513966   
999996  +Gelenek görenek adı altında yapılan bu saçma ...   1607126400   
999997  Not the worst, I suppose. I didn't see Saturda...   1605312000   
999998  Sector Movers: Health Care 0.27%, Technology 0...   1606694400   
999999  An usable, blurry shot intensely cropped looks...   1607644800   

                                        text_preprocessed  type  
0       [chill, fool, manipulation, manifestation, int...     1  
1       [thanks, lot, mornings, pic.twitter.com/tucjmy...     1  
2       [@kendallgbarran1, othersbien, que, las, conoc...     1  
3       [has, spread, the, country, tier, tier, benche...     1  
4       [days, ignite, awards, program, information, c...     1  
...                                                   ...   ...  
999995  [hour, channel, people, vaccines, votes, final...     1  
999996  [gelenek, görenek, adı, altında, yapılan, işle...     1  
999997       [saturday, night, fever, grease, years, was]     1  
999998  [sector, movers, health, care, technology, con...     1  
999999  [shot, looks, watercolor, people, ball, ball, ...     1  

[1000000 rows x 4 columns]

In [80]:
# now join them together before we extract phrases.
# do this by adding a label, calling their columns the same thing (text and created at), and stacking one on top of the other

df["type"]  = 1
df2["type"] = 2

df_all = pd.concat([df.drop('tweet',axis=1),df2.drop('body',axis=1)])



In [82]:
# the last thing I want to do before grouping is: 
# i've nooticed in earlier iterations that hashtags and user tags tend to group together.
# Let's remove these and then add them back in once phrasing is done.

hash_or_user_tag = lambda w: (w[0] == '#' or w[0] == '@')

filter_out  = lambda words: [word for word in words if not hash_or_user_tag(word)]
filter_only = lambda words: [word for word in words if hash_or_user_tag(word)]

df_all['text_preprocessed_no_@#'] = df_all['text_preprocessed'].apply(filter_out)
df_all['text_preprocessed_only_@#'] = df_all['text_preprocessed'].apply(filter_only)



In [83]:
df_all

created_utc                                  text_preprocessed  type  \
0        1605312000  [chill, fool, manipulation, manifestation, int...     1   
1        1605830400  [thanks, lot, mornings, pic.twitter.com/tucjmy...     1   
2        1610328107  [@kendallgbarran1, othersbien, que, las, conoc...     1   
3        1610190443  [has, spread, the, country, tier, tier, benche...     1   
4        1607904000  [days, ignite, awards, program, information, c...     1   
...             ...                                                ...   ...   
999995   1608106941  [lot, thinking, capitalism, change, millennial...     2   
999996   1607373073  [way, party, system, consensus, parties, conse...     2   
999997   1608080667  [roomate, clothes, rack, lets, load, laundry, ...     2   
999998   1605980121                                            [aeons]     2   
999999   1609490595  [post, tag, title, please, rule, moderators, q...     2   

                                  text_preprocessed_no_@#  \
0       [chill, fool, manipulation, manifestation, int...   
1       [thanks, lot, mornings, pic.twitter.com/tucjmy...   
2       [othersbien, que, las, conoces, rey, seguro, s...   
3       [has, spread, the, country, tier, tier, benche...   
4       [days, ignite, awards, program, information, c...   
...                                                   ...   
999995  [lot, thinking, capitalism, change, millennial...   
999996  [way, party, system, consensus, parties, conse...   
999997  [roomate, clothes, rack, lets, load, laundry, ...   
999998                                            [aeons]   
999999  [post, tag, title, please, rule, moderators, q...   

       text_preprocessed_only_@#  
0                             []  
1                             []  
2             [@kendallgbarran1]  
3                             []  
4                             []  
...                          ...  
999995                        []  
999996                        []  
999997                        []  
999998                        []  
999999                        []  

[2000000 rows x 5 columns]

In [84]:
from gensim.models.phrases import Phrases, Phraser

phrases = Phrases(df_all['text_preprocessed_no_@#'], min_count=4, threshold=2)
phraser = Phraser(phrases)

def sentence_to_bi_grams(phrases_model, sentence):
    return phrases_model[sentence]

apply_phrases = lambda sentence: sentence_to_bi_grams(phraser,sentence)

df_all['text_with_phrases'] = df_all['text_preprocessed_no_@#'].apply(apply_phrases) + df_all['text_preprocessed_only_@#']

In [85]:
# what are some examples of phrases that we extracted ? 

for phrase, score in sorted(phrases.find_phrases(df_all['text_preprocessed']).items(),key=lambda tup: tup[1],reverse=True):
    print(phrase, score)

audemars_piguet 484705.5625
shingeki_kyojin 474813.61224489793
gêne_occasionnée 474813.61224489793
kawaski_trawick 474813.61224489793
<username>_spambotdetector 474813.61224489793
twitch.tv/epicenter_ua_twitch.tv/epic_brazil 448653.0826446281
gleb_savchenko 448653.0826446281
dunk'n_divaz 430849.3888888889
личных_сообщениях 430849.3888888889
ishaan_khatter 430849.3888888889
onyeka_okongwu 430849.3888888889
toxoplasma_gondii 430849.3888888889
darrion_cockrell 430849.3888888889
rusten_sheskey 430849.3888888889
𝐅𝐨𝐫_𝐈𝐧𝐟𝐨 415461.9107142857
truth-o-meter_politifact.com 415461.9107142857
ispreview_ispreview.co.uk/index.php/2020… 415461.9107142857
otcpink_gtch 415461.9107142857
escaliers_intérieurs 415461.9107142857
hạnh_phúc 415461.9107142857
burkina_faso 411265.32575757575
kaley_cuoco 387764.45
defn_dfmtf 387764.45
color.gray_transp 387764.45
hocus_pocus 382977.23456790124
feedmysheep_feedmysheep 382977.23456790124
𝕋𝕦𝕩_𝕄𝕒𝕔𝕙𝕚𝕟𝕖𝕤 379147.46222222224
jacobinmag_jacobinmag 376993.2152777778
네이버_tv

shia_labeouf 71808.23148148147
ammonium_nitrate 71808.23148148147
bit.ly/tiorr1_bit.ly/tiorrad1 71808.23148148147
dilip_chhabria 71808.23148148147
goodwood_speedweek 71808.23148148147
zac_efron 71808.23148148147
mohan_گیتا 71808.23148148147
tarafınıza_dönüş 71808.23148148147
shamima_begum 71808.23148148147
pontiac_firebird 71808.23148148147
gish_gallop 71808.23148148147
前日比_いいねされた数 71477.31797235023
siemens_gamesa 71455.36547911548
vroom_vroom 71214.77502295683
devi_sridhar 70932.5213414634
jamaal_bowman 70502.62727272727
raul_jimenez 70502.62727272727
punky_brewster 70502.62727272727
dalai_lama 70471.37610815602
howie_roseman 70247.1829710145
carpe_diem 70247.1829710145
skincare.com_l'oréal 70183.61085972852
मुख्य_सचिव 70183.61085972852
arvind_kejriwal 70127.61329787233
ven_retroalimentación 69867.46846846846
banjo_kazooie 69867.46846846846
jolli_bouquet 69367.52236135957
peço_desculpas 69243.65178571428
chhath_puja 69243.65178571428
sdn_bhd 69243.65178571428
steny_hoyer 69243.6517857

suresh_raina 27697.460714285713
kyrie_irving 27686.160240718073
deu_certo 27648.089126559713
acs_चिकित्सा 27648.089126559713
spector_eccentric 27648.089126559713
saddam_hussein 27636.72066885965
canmake_mermaid 27587.984584980237
tic_toc 27579.26386913229
rex_ankylosaurus 27574.36088888889
timothy_mcveigh 27540.08877840909
mariah_carey 27488.84005316792
seth_godin 27456.08850762527
harold_bornstein 27355.516754850087
paolo_rossi 27339.44418331375
mick_jagger 27293.626445449976
क्लिक_करें 27243.403981264637
herbert_diess 27211.540350877192
ashish_jha 27116.395104895106
maison_margiela 27116.395104895106
blackrock_pre-authorized 27116.395104895106
usain_bolt 27089.332834331337
laverne_shirley 27080.886948930598
roller_coaster 27035.94296098502
morti_bollettino 27021.912891986063
sécurité_globale 26974.918260869566
lennox_hanna 26974.918260869566
cystic_fibrosis 26928.086805555555
alamin_kung 26928.086805555555
aguardamos_resposta 26928.086805555555
omah_lay 26892.17311283009
sasuke_sasuk

nestwealth_rbc 14238.596695226439
jared_leto 14234.785361936445
ana_armas 14203.826007326008
black-eyed_peas 14203.826007326008
colin_kaepernick 14192.685751633986
leo_bit.ly/xjqyj7 14173.148197374978
hal_ketchum 14151.987226277372
dennis_rodman 14143.384194528875
roche_possay 14126.20947176685
foh_boh 14100.525454545455
straw_camel's 14083.454600484261
bullbitcoin_<-- 14080.045388525781
bitaroo_<-- 14080.045388525781
autocoin_<-- 14080.045388525781
vito_corleone 14074.934664246823
wilbur_soot 14068.551473922904
completo_cpf 14049.436594202898
casos_activos 14049.436594202898
medium.com_self-publishing 14003.77211989888
rdt_supports 13985.159659375522
dalton_mcguinty 13981.891225961539
priti_patel 13976.53592897662
respon_melalui 13965.106242496999
redress_grievances 13951.313544973544
joyce_alene 13948.361510791368
volkswagen_beetle 13931.656886227545
ruben_dias 13914.992224880383
alexeï_navalny 13898.367383512545
yee_haw 13898.367383512545
+1 (424) 388 0012_gabriel 13898.367383512545

dijon_mustard 8616.987777777778
miguel_ángel 8616.987777777778
inbound_outbound 8616.987777777778
tulip_mania 8616.987777777778
kisan_morcha 8616.987777777778
peppa_pig 8616.987777777778
mohammed_siraj 8611.246946480125
пожалуйста_номер 8604.24075443787
amino_acids 8594.518448500652
cali_jae 8588.359911406422
talbert_swan 8588.359911406422
diskon_hingga 8588.359911406422
jun_guruji 8578.859513274336
hayden_christensen 8553.627573529411
treasure_trove 8549.137480314961
muchísimas_gracias 8548.598985890652
satanic_temple 8545.51618784309
pvt_ltd 8539.357257257258
allison_arwady 8531.67106710671
phil_spector 8528.331674494893
derangement_syndrome 8526.980758658605
jaime_harrison 8522.295604395604
annonce_vente 8522.295604395604
salmans_bday 8522.295604395604
adjusted_ebitda 8520.422983959568
europa_clipper 8518.135342933854
gute_nacht 8503.606359649122
judd_deere 8503.606359649122
marcus_rashford 8496.699257636146
landfall_nicaragua 8480.359759431383
jen_psaki 8475.725683060109
peaks_vall

...

accusation_evidence 2.186616152217775
razor_evidence 2.186616152217775
thank_i'll 2.186611475180068
attack_terrorists 2.1865890256775775
online_course 2.1865675874364796
executives_share 2.1864792933607373
views_youtube 2.186441280051875
waste_crisis 2.186438608896091
crisis_waste 2.186438608896091
anyone_thinking 2.1864093293471027
starts_christmas 2.186405322732975
emails_tweets 2.186290678150537
online_reputation 2.1862635596851674
houses_places 2.1861881656690194
pay_employees 2.1861865222606385
rate_capital 2.1861865222606385
goods_industries 2.18610764156387
states_democracy 2.186107230741808
garbage_fire 2.1860926466586585
fee_trade 2.186091572216025
says_study 2.186091003393882
britain_countries 2.185893829554551
countries_philippines 2.185893829554551
game_packers 2.1858445416521044
isolation_rules 2.185704904664918
that's_preference 2.185573497914553
wage_staff 2.1855202210858065
spirit_holiday 2.185509032255277
investment_savings 2.1854421362904213
law_practice 2.18544120370

companies_entities 2.147611619950508
crowd_capitol 2.1475913996161893
term_traders 2.1475657141102964
ops_case 2.147550761860588
truck_fuel 2.1474930787118955
ipo_company 2.147462553488424
summary_study 2.1473991272276183
research_mrna 2.1473717758088964
profit_greedy 2.1473111294961718
businesses_restrictions 2.147301832859781
care_needs 2.1472764972317293
island_saturday 2.1472326511174606
cash_reward 2.1471841400796756
omg_pls 2.1471506116728656
medication_term 2.1471078109729596
sub_topics 2.14710424432499
new_years 2.146947587310752
ban_muslims 2.1469419743766283
that's_perfect 2.146928779876771
deaths_today 2.146913668807583
conversation_founder 2.146855499863041
chart_week 2.1468528255046024
money_stock 2.146818633923863
trump_washingtonpost.com 2.1468103932422533
gays_women 2.146795774111798
women_gays 2.146795774111798
vote_ballots 2.146711193078519
price_closing 2.146693267509396
doesn't_immunity 2.14660443637195
end_siege 2.1465527453815545
money_consultant 2.146529500101112

wednesday_violence 2.1121237650232993
yolo_type 2.1120689279532185
stars_moon 2.1119694231992083
senate_january 2.1119414879597365
not_take 2.1118204711784694
block_party 2.1117944139230684
phone_plans 2.111628730962014
panel_event 2.1116265008190247
justice_address 2.111575522428698
crypto_liquidity 2.1115347031614116
vacations_year 2.1115190370307295
museum_history 2.1113047649460785
thank_panelists 2.111211079484203
rebecca_thank 2.111211079484203
life_soul 2.111124519562484
asset_income 2.111114816275204
population_india 2.1110959861108585
housing_developers 2.111034938844195
kind_relationship 2.11101186914965
guidelines_travel 2.11093083908302
gop_doesn't 2.1108899884075494
workers_health 2.1108843630201113
plant_growth 2.1108696290032425
hello_james 2.1108036731786597
we're_experience 2.110768628642131
modern_family 2.110742202384192
commission_rate 2.1106721903616568
information_email 2.1106639328395707
service_jobs 2.1106298198402547
trump_threat 2.110617054049024
labour_wages 

refund_delay 2.078151947307212
top_priority 2.0781408098953866
schools_class 2.0780840109519385
water_mark 2.0780331312015665
again_you're 2.0779988183580533
pre_season 2.077962627540084
shopping_clothes 2.0779281082422214
house_officials 2.077881133217527
states_europe 2.0778579596543514
stocks_market 2.077855038088868
episode_youtube 2.0778006194856946
housing_lottery 2.07777890898569
taxes_repairs 2.0777544156329184
discovery_center 2.0777132235691504
billions_devices 2.0776926281497436
research_journal 2.077680196877979
journal_research 2.077680196877979
update_new 2.077668415138311
yea_shit 2.0776625150417294
workers_job 2.077598630523737
services_economy 2.07754033544364
research_claims 2.0775181186973968
quicker_response 2.077493931157819
courts_police 2.0773861306877257
executives_employees 2.077355923123284
cause_deaths 2.077308440727621
advice_advisor 2.077298425187008
window_period 2.0772390758170705
catalyst_price 2.0772209934799655
conclusion_data 2.0771788025843017
wiscon

year_homicides 2.0342683405539956
movie_event 2.0342506936841764
all_christmas 2.0341782682033154
fun_read 2.0341059898903207
lots_land 2.034077352765517
thanks_brian 2.033956023077161
data_access 2.033947157061374
attention_please 2.0339029358391807
hill_wednesday 2.033855148753061
leadership_management 2.0338412807975823
twitter_updates 2.033815412232203
places_cities 2.0336924788699227
list_reasons 2.033666042710153
close_friday 2.033647149276463
production_china 2.0336398256258823
brexit_impact 2.033587127708562
stock_merger 2.0335294084330715
gonna_stop 2.0334340606063344
actors_advantage 2.0332888499695874
policies_economy 2.0332158193239804
recommend_trading 2.0331587844391943
that's_nonsense 2.033091625967026
pension_etc 2.0329946271173287
trials_patients 2.0329903636439894
lack_space 2.032987592395908
level_volatility 2.0328804521450445
market_order 2.0328282181804647
bonus_entry 2.0328246349767536
dollars_billions 2.0327852051254163
sound_rocket 2.0327772127744343
hit_pandemi

In [86]:
from gensim.models import Word2Vec


model = Word2Vec(sentences=df_all["text_with_phrases"], vector_size=100, window=10, min_count=2, workers=4)

# created_utc of 1610496000 is Wednesday, January 13, 2021 12:00:00 AM (GMT)
model_st = Word2Vec(sentences=df_all[df_all.created_utc > 1610496000]["text_with_phrases"])


from collections import defaultdict

def w2v_based_top_trends(qt: str, k: int, k_inner: int = 200):
    # ensure the query term has been , and 
    assert k < k_inner
    parsed_qt = qt.lower().strip().replace(" ","_")
    
    # do a full join on these lists. i don't know a way to do in a fancy or less-verbose way in python so here:
    try:
        long_term_trends  = model.wv.most_similar(parsed_qt, topn=k)
        short_term_trends = model_st.wv.most_similar(parsed_qt, topn=k)
    except KeyError:
        return [("did not find that trend",0)]
    
    st_scores = defaultdict(int)
    lt_scores = defaultdict(int)
    
    for word, relevance in short_term_trends:
        st_scores[word] = relevance
    
    for word, relevance in long_term_trends:
        lt_scores[word] = relevance

    
    # do a full join on these lists
    all_words = set([w for w,_ in long_term_trends] + [w for w,_ in short_term_trends])
    
    joined_list = [(word,st_scores[word],lt_scores[word]) for word in all_words]
        
    return [w for w, st_score, lt_score in sorted(joined_list,key= lambda tup: tup[1] + tup[2],reverse=True)[:k]]
    

In [87]:
#We just tried the w2v approach. Now let's see if an RS can also work as a top k trend generator
#from a notebook I found on the MS recommenders github:
# 'SAR is intended to be used on interactions with the following schema:
# <User ID>, <Item ID>,<Time>,[<Event Type>], [<Event Weight>].

# step 1 is make my data look like that schema
K = 5
print(w2v_based_top_trends("augmented_reality",K))
print(w2v_based_top_trends("iPhone",K))
print(w2v_based_top_trends("elon musk",K))
print(w2v_based_top_trends("denim",K))
print(w2v_based_top_trends("biden",K))
print(w2v_based_top_trends("bitcoin",K))
print(w2v_based_top_trends("student loans",K))
print(w2v_based_top_trends("index funds",K))
print(w2v_based_top_trends("perfume",K))
print(w2v_based_top_trends("gold",K))

['quality', 'servers', 'resource', 'domain', 'manage']
['copy', 'download', 'rocket', 'plastic', 'seafood']
['bits', 'upgrade', 'eggs', 'fundamentals', 'fud']
['atau', 'kak', 'saya', '#climateaction', 'toyota']
['joe_biden', 'office', 'president_donald', 'president', 'president_trump']
['btc', 'crypto', 'cash', 'car', 'option']
['end_day', 'bills', "hasn't", 'bunch_people', 'sign']
['features', 'holdings', 'storage', 'cryptocurrency', 'etf']
['giveaway', 'andrew', 'gem', 'charlotte', 'balm']
['market_cap', 'penny_stocks', 'exchanges', 'holders', 'premium']


In [44]:
# this seems like an uphill battle as I do not see too many notebooks that use the recommenders library




In [45]:
# a good way to end: 

# have a set of train and test queries to run these strategies on.
# have a table with <strategy> <k>, <map@k>, <ndcg@k>, <diversity score>
# strategy 1: w2v
# strategy 2: association rule mining
# strategy 3: item-based recommendation
